#Define the Gpu

In [ ]:
import torch

if torch.cuda.is_available():
    print("GPU is available")
else:
    print("GPU is not available")


GPU is not available


#Import needed libraries

In [ ]:
import torch
import requests
import numpy as np
import pandas as pd
from tqdm import tqdm
from itertools import product
from IPython.display import display, clear_output
from torch.utils.data import Dataset, DataLoader, SequentialSampler, BatchSampler

pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)

In [ ]:
# for reproducibility
import os
import random

def seed_everything(seed=42):
  random.seed(seed)
  os.environ['PYTHONHASHSEED'] = str(seed)
  np.random.seed(seed)
  torch.manual_seed(seed)
  torch.cuda.manual_seed(seed)
  torch.backends.cudnn.deterministic = True
seed_everything()

#Reading the data

In [ ]:
ratings=pd.read_csv("/content/ratings.csv")
movies=pd.read_csv("/content/movies.csv")

In [ ]:
ratings.head(),movies.head()

(   userId  movieId  rating    timestamp
 0       1        1     4.0  964982703.0
 1       1        3     4.0  964981247.0
 2       1        6     4.0  964982224.0
 3       1       47     5.0  964983815.0
 4       1       50     5.0  964982931.0,
    movieId                               title  \
 0        1                    Toy Story (1995)   
 1        2                      Jumanji (1995)   
 2        3             Grumpier Old Men (1995)   
 3        4            Waiting to Exhale (1995)   
 4        5  Father of the Bride Part II (1995)   
 
                                         genres  
 0  Adventure|Animation|Children|Comedy|Fantasy  
 1                   Adventure|Children|Fantasy  
 2                               Comedy|Romance  
 3                         Comedy|Drama|Romance  
 4                                       Comedy  )

knowing the shape

In [ ]:
ratings.shape,movies.shape

((85271, 4), (9742, 3))

In [ ]:
ratings

userId  movieId  rating    timestamp
0           1        1     4.0  964982703.0
1           1        3     4.0  964981247.0
2           1        6     4.0  964982224.0
3           1       47     5.0  964983815.0
4           1       50     5.0  964982931.0
...       ...      ...     ...          ...
85266     554     2243     3.0  944902081.0
85267     554     2282     5.0  944902251.0
85268     554     2324     5.0  944898992.0
85269     554     2396     5.0  944898992.0
85270     554      249     NaN          NaN

[85271 rows x 4 columns]

#Merging the dataframes

In [ ]:
df = pd.merge(ratings, movies, on='movieId', how='left')
df

userId  movieId  rating    timestamp  \
0           1        1     4.0  964982703.0   
1           1        3     4.0  964981247.0   
2           1        6     4.0  964982224.0   
3           1       47     5.0  964983815.0   
4           1       50     5.0  964982931.0   
...       ...      ...     ...          ...   
85266     554     2243     3.0  944902081.0   
85267     554     2282     5.0  944902251.0   
85268     554     2324     5.0  944898992.0   
85269     554     2396     5.0  944898992.0   
85270     554      249     NaN          NaN   

                                            title  \
0                                Toy Story (1995)   
1                         Grumpier Old Men (1995)   
2                                     Heat (1995)   
3                     Seven (a.k.a. Se7en) (1995)   
4                      Usual Suspects, The (1995)   
...                                           ...   
85266                       Broadcast News (1987)   
85267                               Pecker (1998)   
85268  Life Is Beautiful (La Vita è bella) (1997)   
85269                  Shakespeare in Love (1998)   
85270                     Immortal Beloved (1994)   

                                            genres  
0      Adventure|Animation|Children|Comedy|Fantasy  
1                                   Comedy|Romance  
2                            Action|Crime|Thriller  
3                                 Mystery|Thriller  
4                           Crime|Mystery|Thriller  
...                                            ...  
85266                         Comedy|Drama|Romance  
85267                                 Comedy|Drama  
85268                     Comedy|Drama|Romance|War  
85269                         Comedy|Drama|Romance  
85270                                Drama|Romance  

[85271 rows x 6 columns]

#Know the number of unique users and items

In [ ]:
df['userId'].nunique()
df['movieId'].nunique()


8757

#Selection of first 100 unique user because of Gpu capability

In [ ]:
first_100_users = df['userId'].unique()[:100]
df = df[df['userId'].isin(first_100_users)]
df

userId  movieId  rating     timestamp  \
0           1        1     4.0  9.649827e+08   
1           1        3     4.0  9.649812e+08   
2           1        6     4.0  9.649822e+08   
3           1       47     5.0  9.649838e+08   
4           1       50     5.0  9.649829e+08   
...       ...      ...     ...           ...   
15443     100     6785     4.5  1.100184e+09   
15444     100     6873     4.0  1.100187e+09   
15445     100     7149     3.5  1.100184e+09   
15446     100     8529     4.0  1.100184e+09   
15447     100     8636     4.5  1.100187e+09   

                                        title  \
0                            Toy Story (1995)   
1                     Grumpier Old Men (1995)   
2                                 Heat (1995)   
3                 Seven (a.k.a. Se7en) (1995)   
4                  Usual Suspects, The (1995)   
...                                       ...   
15443  Seven Brides for Seven Brothers (1954)   
15444              Intolerable Cruelty (2003)   
15445           Something's Gotta Give (2003)   
15446                    Terminal, The (2004)   
15447                     Spider-Man 2 (2004)   

                                            genres  
0      Adventure|Animation|Children|Comedy|Fantasy  
1                                   Comedy|Romance  
2                            Action|Crime|Thriller  
3                                 Mystery|Thriller  
4                           Crime|Mystery|Thriller  
...                                            ...  
15443               Comedy|Musical|Romance|Western  
15444                               Comedy|Romance  
15445                         Comedy|Drama|Romance  
15446                         Comedy|Drama|Romance  
15447                 Action|Adventure|Sci-Fi|IMAX  

[15448 rows x 6 columns]

#Splitting the genre column to be used as categorical features

In [ ]:
genres_unique = pd.DataFrame(df.genres.str.split('|').tolist()).stack().unique()
genres_unique = pd.DataFrame(genres_unique, columns=['genre']) # Format into DataFrame to store later
df = df.join(df.genres.str.get_dummies().astype(int))
df.drop('genres', inplace=True, axis=1)
df.head()

userId  movieId  rating    timestamp                        title  \
0       1        1     4.0  964982703.0             Toy Story (1995)   
1       1        3     4.0  964981247.0      Grumpier Old Men (1995)   
2       1        6     4.0  964982224.0                  Heat (1995)   
3       1       47     5.0  964983815.0  Seven (a.k.a. Se7en) (1995)   
4       1       50     5.0  964982931.0   Usual Suspects, The (1995)   

   (no genres listed)  Action  Adventure  Animation  Children  Comedy  Crime  \
0                   0       0          1          1         1       1      0   
1                   0       0          0          0         0       1      0   
2                   0       1          0          0         0       0      1   
3                   0       0          0          0         0       0      0   
4                   0       0          0          0         0       0      1   

   Documentary  Drama  Fantasy  Film-Noir  Horror  IMAX  Musical  Mystery  \
0            0      0        1          0       0     0        0        0   
1            0      0        0          0       0     0        0        0   
2            0      0        0          0       0     0        0        0   
3            0      0        0          0       0     0        0        1   
4            0      0        0          0       0     0        0        1   

   Romance  Sci-Fi  Thriller  War  Western  
0        0       0         0    0        0  
1        1       0         0    0        0  
2        0       0         1    0        0  
3        0       0         1    0        0  
4        0       0         1    0        0

In [ ]:
df.shape

(15448, 25)

In [ ]:
genres_unique = ['Adventure', 'Animation', 'Children', 'Comedy', 'Fantasy', 'Romance', 'Drama', 'Action', 'Crime', 'Thriller', 'Horror', 'Mystery', 'Sci-Fi', 'War', 'Musical', 'Documentary', 'IMAX', 'Western', 'Film-Noir', '(no genres listed)']
cats_ohe = pd.get_dummies(df[genres_unique])


#Get some insights from data

In [ ]:
null_counts = ratings.isnull().sum()
null_percentages = (null_counts / len(ratings)) * 100
null_summary = pd.DataFrame({'Null Count': null_counts, 'Null Percentage': null_percentages})
null_summary


Null Count  Null Percentage
userId              0         0.000000
movieId             0         0.000000
rating              1         0.001173
timestamp           1         0.001173

In [ ]:
null_counts = movies.isnull().sum()
null_percentages = (null_counts / len(ratings)) * 100
null_summary = pd.DataFrame({'Null Count': null_counts, 'Null Percentage': null_percentages})
null_summary


Null Count  Null Percentage
movieId           0              0.0
title             0              0.0
genres            0              0.0

In [ ]:
unique_items = ratings['movieId'].nunique()
unique_users = ratings['userId'].nunique()
print("Unique Users:", unique_users)
print("Unique movies:", unique_items)


Unique Users: 554
Unique movies: 8757


In [ ]:
unique_items = movies['movieId'].nunique()
print("Unique movies:", unique_items)


Unique movies: 9742


#Mapping of users and Movies

In [ ]:
user_mappings = df['userId'].drop_duplicates().reset_index(drop=True).reset_index().rename(columns={'index': 'new_id'}).set_index('userId')
user_mappings

new_id
userId        
1            0
2            1
3            2
4            3
5            4
...        ...
96          95
97          96
98          97
99          98
100         99

[100 rows x 1 columns]

In [ ]:
movie_mappings = df['movieId'].drop_duplicates().reset_index(drop=True).reset_index().rename(columns={'index': 'new_id'}).set_index('movieId')
movie_mappings

new_id
movieId        
1             0
3             1
6             2
47            3
50            4
...         ...
2262       4175
3244       4176
5380       4177
6183       4178
6785       4179

[4180 rows x 1 columns]

#Create Aggregated History Matrix

In [ ]:
df_copy = df.copy() # To avoid changing the original DataFrame
df_copy['ones'] = 1

In [ ]:
columns_to_replace = ["userId", "movieId"]  # Specify the columns you want to replace

df_mapped = df_copy.copy()  # Create a copy of the original dataframe

# Replace values in the specified columns
df_mapped[columns_to_replace] = df_mapped[columns_to_replace].replace({
    "userId": user_mappings.new_id.to_dict(),
    "movieId": movie_mappings.new_id.to_dict()
})

df_mapped

userId  movieId  rating     timestamp  \
0           0        0     4.0  9.649827e+08   
1           0        1     4.0  9.649812e+08   
2           0        2     4.0  9.649822e+08   
3           0        3     5.0  9.649838e+08   
4           0        4     5.0  9.649829e+08   
...       ...      ...     ...           ...   
15443      99     4179     4.5  1.100184e+09   
15444      99     2962     4.0  1.100187e+09   
15445      99      878     3.5  1.100184e+09   
15446      99      886     4.0  1.100184e+09   
15447      99      782     4.5  1.100187e+09   

                                        title  (no genres listed)  Action  \
0                            Toy Story (1995)                   0       0   
1                     Grumpier Old Men (1995)                   0       0   
2                                 Heat (1995)                   0       1   
3                 Seven (a.k.a. Se7en) (1995)                   0       0   
4                  Usual Suspects, The (1995)                   0       0   
...                                       ...                 ...     ...   
15443  Seven Brides for Seven Brothers (1954)                   0       0   
15444              Intolerable Cruelty (2003)                   0       0   
15445           Something's Gotta Give (2003)                   0       0   
15446                    Terminal, The (2004)                   0       0   
15447                     Spider-Man 2 (2004)                   0       1   

       Adventure  Animation  Children  Comedy  Crime  Documentary  Drama  \
0              1          1         1       1      0            0      0   
1              0          0         0       1      0            0      0   
2              0          0         0       0      1            0      0   
3              0          0         0       0      0            0      0   
4              0          0         0       0      1            0      0   
...          ...        ...       ...     ...    ...          ...    ...   
15443          0          0         0       1      0            0      0   
15444          0          0         0       1      0            0      0   
15445          0          0         0       1      0            0      1   
15446          0          0         0       1      0            0      1   
15447          1          0         0       0      0            0      0   

       Fantasy  Film-Noir  Horror  IMAX  Musical  Mystery  Romance  Sci-Fi  \
0            1          0       0     0        0        0        0       0   
1            0          0       0     0        0        0        1       0   
2            0          0       0     0        0        0        0       0   
3            0          0       0     0        0        1        0       0   
4            0          0       0     0        0        1        0       0   
...        ...        ...     ...   ...      ...      ...      ...     ...   
15443        0          0       0     0        1        0        1       0   
15444        0          0       0     0        0        0        1       0   
15445        0          0       0     0        0        0        1       0   
15446        0          0       0     0        0        0        1       0   
15447        0          0       0     1        0        0        0       1   

       Thriller  War  Western  ones  
0             0    0        0     1  
1             0    0        0     1  
2             1    0        0     1  
3             1    0        0     1  
4             1    0        0     1  
...         ...  ...      ...   ...  
15443         0    0        1     1  
15444         0    0        0     1  
15445         0    0        0     1  
15446         0    0        0     1  
15447         0    0        0     1  

[15448 rows x 26 columns]

In [ ]:
# Replace None with the appropriate values
agg_history = pd.pivot_table(df_mapped,
               values='ones', index='userId', columns='movieId', fill_value=0)

agg_history

movieId  0     1     2     3     4     5     6     7     8     9     10    \
userId                                                                      
0           1     1     1     1     1     1     1     1     1     1     1   
1           0     0     0     0     0     0     0     0     0     0     0   
2           0     0     0     0     0     0     0     0     0     0     0   
3           0     0     0     1     0     0     0     0     0     0     0   
4           1     0     0     0     1     0     0     1     0     0     0   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
95          1     0     0     0     1     0     0     1     0     0     0   
96          0     0     0     0     0     0     0     0     0     0     0   
97          1     0     0     0     0     0     0     0     0     0     0   
98          0     0     0     0     0     0     0     0     0     0     1   
99          0     1     0     0     0     0     0     0     0     0     0   

movieId  11    12    13    14    15    16    17    18    19    20    21    \
userId                                                                      
0           1     1     1     1     1     1     1     1     1     1     1   
1           0     0     0     0     0     0     0     1     0     0     0   
2           0     0     0     0     0     0     0     0     0     0     0   
3           0     0     0     1     1     1     0     0     0     0     0   
4           0     0     0     0     0     1     1     0     1     0     0   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
95          0     0     0     0     1     1     0     0     0     0     0   
96          0     0     0     0     0     0     0     0     0     0     0   
97          0     0     0     0     0     0     0     0     0     1     0   
98          0     0     1     0     0     1     1     1     1     0     0   
99          0     1     0     1     0     1     0     0     0     1     0   

movieId  22    23    24    25    26    27    28    29    30    31    32    \
userId                                                                      
0           1     1     1     1     1     1     1     1     1     1     1   
1           0     0     0     0     0     0     0     0     0     0     0   
2           0     0     0     0     0     0     1     0     0     0     0   
3           0     0     1     1     0     0     0     0     0     1     0   
4           1     0     0     1     0     0     1     0     0     0     1   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
95          1     0     0     0     1     0     1     0     0     0     0   
96          0     0     0     0     0     0     0     0     0     0     0   
97          0     0     0     0     0     0     0     0     0     0     0   
98          0     0     0     0     0     0     0     0     0     0     0   
99          0     0     1     0     0     0     0     0     0     1     1   

movieId  33    34    35    36    37    38    39    40    41    42    43    \
userId                                                                      
0           1     1     1     1     1     1     1     1     1     1     1   
1           0     0     0     0     0     0     0     0     0     0     0   
2           0     0     0     0     0     0     0     0     0     0     0   
3           0     1     0     1     1     0     0     0     0     0     0   
4           1     0     1     1     0     0     0     0     0     0     0   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
95          0     0     0     0     1     0     0     1     0     1     0   
96          0     1     0     0     0     0     0     0     0     0     0   
97          0     1     0     1     0     0     0     0     0     0     0   
98          1     0     0     0     0     0     0     0     0     0     0   
99          1     0     0     0     1     0     0     0     0     0   

#Normalize Aggregated History Matrix

In [ ]:
# Replace None with correct values
# We need to normalize the aggregated history by dividing each value by the sum of all the values in the same row
agg_history_norm = agg_history / agg_history.values.sum(axis=1, keepdims=True)
agg_history_norm


movieId      0         1        2        3         4        5        6     \
userId                                                                      
0        0.004310  0.004310  0.00431  0.00431  0.004310  0.00431  0.00431   
1        0.000000  0.000000  0.00000  0.00000  0.000000  0.00000  0.00000   
2        0.000000  0.000000  0.00000  0.00000  0.000000  0.00000  0.00000   
3        0.000000  0.000000  0.00000  0.00463  0.000000  0.00000  0.00000   
4        0.022727  0.000000  0.00000  0.00000  0.022727  0.00000  0.00000   
...           ...       ...      ...      ...       ...      ...      ...   
95       0.012821  0.000000  0.00000  0.00000  0.012821  0.00000  0.00000   
96       0.000000  0.000000  0.00000  0.00000  0.000000  0.00000  0.00000   
97       0.010870  0.000000  0.00000  0.00000  0.000000  0.00000  0.00000   
98       0.000000  0.000000  0.00000  0.00000  0.000000  0.00000  0.00000   
99       0.000000  0.006757  0.00000  0.00000  0.000000  0.00000  0.00000   

movieId      7        8        9         10       11        12        13    \
userId                                                                       
0        0.004310  0.00431  0.00431  0.004310  0.00431  0.004310  0.004310   
1        0.000000  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
2        0.000000  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
3        0.000000  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
4        0.022727  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
...           ...      ...      ...       ...      ...       ...       ...   
95       0.012821  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
96       0.000000  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
97       0.000000  0.00000  0.00000  0.000000  0.00000  0.000000  0.000000   
98       0.000000  0.00000  0.00000  0.018868  0.00000  0.000000  0.018868   
99       0.000000  0.00000  0.00000  0.000000  0.00000  0.006757  0.000000   

movieId      14        15        16        17        18        19        20    \
userId                                                                          
0        0.004310  0.004310  0.004310  0.004310  0.004310  0.004310  0.004310   
1        0.000000  0.000000  0.000000  0.000000  0.034483  0.000000  0.000000   
2        0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3        0.004630  0.004630  0.004630  0.000000  0.000000  0.000000  0.000000   
4        0.000000  0.000000  0.022727  0.022727  0.000000  0.022727  0.000000   
...           ...       ...       ...       ...       ...       ...       ...   
95       0.000000  0.012821  0.012821  0.000000  0.000000  0.000000  0.000000   
96       0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
97       0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.010870   
98       0.000000  0.000000  0.018868  0.018868  0.018868  0.018868  0.000000   
99       0.006757  0.000000  0.006757  0.000000  0.000000  0.000000  0.006757   

movieId     21        22       23        24        25        26       27    \
userId                                                                       
0        0.00431  0.004310  0.00431  0.004310  0.004310  0.004310  0.00431   
1        0.00000  0.000000  0.00000  0.000000  0.000000  0.000000  0.00000   
2        0.00000  0.000000  0.00000  0.000000  0.000000  0.000000  0.00000   
3        0.00000  0.000000  0.00000  0.004630  0.004630  0.000000  0.00000   
4        0.00000  0.022727  0.00000  0.000000  0.022727  0.000000  0.00000   
...          ...       ...      ...       ...       ...       ...      ...   
95       0.00000  0.012821  0.00000  0.000000  0.000000  0.012821  0.00000   
96       0.00000  0.000000  0.00000  0.000000  0.000000  0.000000  0.00000   
97       0.00000  0.000000  0.00000  0.000000  0.000000  0.000000  0.00000   
98       0.00000  0.000000  0.00000  0.000000  0.000000  0.000000  0.00

#Check the null values and the final shape

In [ ]:
df.isnull().sum()

userId                0
movieId               0
rating                0
timestamp             0
title                 0
(no genres listed)    0
Action                0
Adventure             0
Animation             0
Children              0
Comedy                0
Crime                 0
Documentary           0
Drama                 0
Fantasy               0
Film-Noir             0
Horror                0
IMAX                  0
Musical               0
Mystery               0
Romance               0
Sci-Fi                0
Thriller              0
War                   0
Western               0
dtype: int64

In [ ]:
df.shape

(15448, 25)

In [ ]:
cats_ohe.shape

(15448, 20)

#Tagging Transactions into Train and Test Sets

In [ ]:
df['Train'] = (ratings.groupby("userId").cumcount(ascending=False) != 0).replace({True:1, False:0})
df[['userId','movieId','Train']].head()

userId  movieId  Train
0       1        1      1
1       1        3      1
2       1        6      1
3       1       47      1
4       1       50      1

#Putting it all together

In [ ]:
final = pd.concat([df_mapped[['userId','movieId']], cats_ohe,df[['Train','rating']]], axis=1)
final

userId  movieId  Adventure  Animation  Children  Comedy  Fantasy  \
0           0        0          1          1         1       1        1   
1           0        1          0          0         0       1        0   
2           0        2          0          0         0       0        0   
3           0        3          0          0         0       0        0   
4           0        4          0          0         0       0        0   
...       ...      ...        ...        ...       ...     ...      ...   
15443      99     4179          0          0         0       1        0   
15444      99     2962          0          0         0       1        0   
15445      99      878          0          0         0       1        0   
15446      99      886          0          0         0       1        0   
15447      99      782          1          0         0       0        0   

       Romance  Drama  Action  Crime  Thriller  Horror  Mystery  Sci-Fi  War  \
0            0      0       0      0         0       0        0       0    0   
1            1      0       0      0         0       0        0       0    0   
2            0      0       1      1         1       0        0       0    0   
3            0      0       0      0         1       0        1       0    0   
4            0      0       0      1         1       0        1       0    0   
...        ...    ...     ...    ...       ...     ...      ...     ...  ...   
15443        1      0       0      0         0       0        0       0    0   
15444        1      0       0      0         0       0        0       0    0   
15445        1      1       0      0         0       0        0       0    0   
15446        1      1       0      0         0       0        0       0    0   
15447        0      0       1      0         0       0        0       1    0   

       Musical  Documentary  IMAX  Western  Film-Noir  (no genres listed)  \
0            0            0     0        0          0                   0   
1            0            0     0        0          0                   0   
2            0            0     0        0          0                   0   
3            0            0     0        0          0                   0   
4            0            0     0        0          0                   0   
...        ...          ...   ...      ...        ...                 ...   
15443        1            0     0        1          0                   0   
15444        0            0     0        0          0                   0   
15445        0            0     0        0          0                   0   
15446        0            0     0        0          0                   0   
15447        0            0     1        0          0                   0   

       Train  rating  
0          1     4.0  
1          1     4.0  
2          1     4.0  
3          1     5.0  
4          1     5.0  
...      ...     ...  
15443      1     4.5  
15444      1     4.0  
15445      1     3.5  
15446      1     4.0  
15447      0     4.5  

[15448 rows x 24 columns]

#Split Data into Training and Test Dataframes

In [ ]:
train = final[final.Train == 1]
test = final[final.Train == 0]
print('The dimensions of the training subset: ', train.shape[0], 'X', train.shape[1])
print('The dimensions of the test subset: ', test.shape[0], 'X', test.shape[1])

The dimensions of the training subset:  15348 X 24
The dimensions of the test subset:  100 X 24


#**Torch Dataset and DataLoader**

#Create Customized Dataset Class

In [ ]:
class DPMovieDataset(Dataset):
  def __init__(self, user_ids, data, agg_hist, active_matrix, recommendation=False):
    self.user_ids = user_ids
    self.data = data
    self.agg_hist = agg_hist
    self.active_matrix = active_matrix
    self.recommendation = recommendation

  def __len__(self):
    return self.user_ids.shape[0]

  def __getitem__(self, idx):
    batch_data = self.data[self.data['userId'].isin(idx)] # Select the rows corresponding to the list of user indices `idx` from self.data dataframe
    cat_cols = batch_data[['Adventure', 'Animation', 'Children', 'Comedy', 'Fantasy', 'Romance', 'Drama', 'Action', 'Crime', 'Thriller', 'Horror', 'Mystery', 'Sci-Fi', 'War', 'Musical', 'Documentary', 'IMAX', 'Western', 'Film-Noir', '(no genres listed)']] # From batch_data extract only the one-hot encoded categorical columns
    agg_history = batch_data[['userId']].merge(self.agg_hist, left_on='userId', right_index=True) # Get the aggregated history for each selected transaction using merge
    active_groups = self.active_matrix[self.active_matrix.index.isin(batch_data.index)] # Select the rows corresponding to the indices of the transactions selected in batch_data

    features = torch.from_numpy(np.hstack((active_groups.values, agg_history.values, cat_cols.values))) # Concatenate the processed columns together horizontally

    if not self.recommendation:
      targets = batch_data['rating']
      return features, targets
    else:
      return features

#Instantiate Train and Test Objects from the Custom Dataset

In [ ]:
active_columns = pd.get_dummies(final[['userId','movieId']].astype(str))
dataset_train = DPMovieDataset(user_mappings.values, train, agg_history_norm, active_columns)
dataset_test = DPMovieDataset(user_mappings.values, test, agg_history_norm, active_columns)

#Create the DataLoader for Train and Test Datasets

In [ ]:
dataloader_train = DataLoader(dataset_train,
                              sampler=BatchSampler(SequentialSampler(dataset_train), batch_size=10, drop_last=False),
                              batch_size=None)

dataloader_test = DataLoader(dataset_test,
                              sampler=BatchSampler(SequentialSampler(dataset_test), batch_size=10, drop_last=False),
                              batch_size=None)

#**Torch Model Implementation**

#Create the Model Class

In [ ]:
class FactorizationMachine(torch.nn.Module):
  def __init__(self, n, k, bias=False):
    super(FactorizationMachine, self).__init__()
    self.n = n
    self.k = k
    self.linear = torch.nn.Linear(self.n, 1, bias)
    self.V = torch.nn.Parameter(torch.randn(n,k)) # Creating the latent matrix V of size (n X k) and initializing it with random values

  def forward(self, x_batch):
    x_batch = x_batch.float()
    part_1 = torch.matmul(x_batch, self.V).pow(2).sum(1, keepdim=True)  # perform the first part of the interaction term: row-wise-sum((XV)^2)
    part_2 = torch.matmul(x_batch.pow(2), self.V.pow(2)).sum(1, keepdim=True) # perform the second part of the interaction term: row-wise-sum((X)^2 * (V)^2))
    inter_term = (part_1 - part_2)/2 # Put the interaction term parts together (refer to the equations above)
    var_strength = self.linear(x_batch) # Perform the linear part of the model equation (refer to the demo notebook on how to use layers in pytorch models)
    return var_strength + inter_term

#Instantiate a Model Object

In [ ]:
features,ratings=dataset_train[[1]]
features.shape

torch.Size([28, 8481])

In [ ]:
model = FactorizationMachine(n=11413, k=5)

#**Training the Model**

#Write a Function to Run a Single Step of Training

In [ ]:
def model_step(mode, x, y=None, optimizer=None, train=True):
  if train: # If we're in training phase, then zero the gradients and make sure the model is set to train
    model.train()
    optimizer.zero_grad()
  else: # If we're in evaluation phase, then make sure the model is set to eval
    model.eval()

  with torch.set_grad_enabled(train): # Either to perform the next lines with gradient tracing or not
    pred = model(x) # Get the model output from x
    pred = pred.reshape(pred.shape[0], ) # Flatten the prediction values

    y = torch.from_numpy(y.values.reshape(y.shape[0], )).float()

    criterion = torch.nn.MSELoss() # Define the criterion as MSELoss from torch
    loss = criterion(pred, y)

    if train:
      loss.backward()
      optimizer.step()

  return loss

#Write a Function to Simulate the Training Loop of the Model

In [ ]:
def train_loop(model, train_loader, eval_loader, lr, w_decay, epochs, eval_step):
  step = 0
  """ Defining our optimizer """
  optimizer = torch.optim.Adam(model.parameters(), lr=lr, weight_decay=w_decay)
  epochs_l, steps, t_losses, v_losses = [], [], [], []

  epochs_tqdm = tqdm(range(epochs), desc='Training in Progress', leave=True)
  for epoch in epochs_tqdm:
    for x, y in train_loader:
      loss_batch = model_step(model, x, y, optimizer, train=True)
      step +=1
      if step % eval_step == 0:
        train_loss = loss_batch
        val_loss = 0
        for x, y in eval_loader:
          val_loss += model_step(model, x, y, train=False)
        epochs_l.append(epoch+1)
        steps.append(step)
        t_losses.append(train_loss.detach().numpy())
        v_losses.append(val_loss.detach().numpy())
        clear_output(wait=True)
        display(pd.DataFrame({'Epoch': epochs_l, 'Step': steps, 'Training Loss': t_losses, 'Validation Loss': v_losses}))

#Train the Model

In [ ]:
#train_loop(model, dataloader_train, dataloader_test, lr=0.01, w_decay=0.01, epochs=150, eval_step=150)

#Mount the Drive and load the Model

In [ ]:
#from google.colab import drive
#drive.mount("/content/mydrive")

import pickle
file_path = "/content/mydrive/MyDrive/fm_model.pkl"  # Change the path as per your preference
with open(file_path, 'rb') as f:
    model = pickle.load(f)

#Evaluating on single Example

In [ ]:
new=user_mappings.loc[2].new_id
features,ratings = dataset_test[[new]]
features.shape,ratings.shape

(torch.Size([1, 8481]), (1,))

In [ ]:
new

1

In [ ]:
model.eval()
with torch.no_grad():
  print(f'Predicted rating for User of interest: {model(features).item()}') # Get the model output on the user of interest after running the previous cell to now their new_id
  print(f'Actual Rating: {ratings.values[0]}') # Extract the actual rating for the user of interest from dataset_test Dataset object

Predicted rating for User of interest: 3.745978832244873
Actual Rating: 5.0


#**Recommending New Items**

In [ ]:
# Replace None with the new_id of the user
items_our_user_rated = (train[train.userId==new].movieId).unique().tolist()
items_our_user_rated.extend((test[test.userId==new].movieId).unique().tolist())

In [ ]:
items_our_user_can_rate = movie_mappings[~movie_mappings.new_id.isin(items_our_user_rated)].new_id.tolist()

In [ ]:
print(f'Number of unique items user of interest rated is {len(items_our_user_rated)}')
print(f'Number of unique items that can be recommended to user of interest is {len(items_our_user_can_rate)}')
print(f'Preview of the item list:\n\t{items_our_user_can_rate[:5]}')

Number of unique items user of interest rated is 29
Number of unique items that can be recommended to user of interest is 4151
Preview of the item list:
	[0, 1, 2, 3, 4]


In [ ]:
N = 5  # Number of recommendations

recommendations = []

model.eval()  # Set the model to evaluation mode

with torch.no_grad():
    for item_id in items_our_user_can_rate:
        features = dataset_test[[item_id]][0]  # Create a dataset for the item
        #print(features)
        # Check if the dataset for the item is empty
        if features.nelement() == 0:
            continue

        predicted_rating = model(features).item()  # Get the predicted rating for the user

        recommendations.append((item_id, predicted_rating))

# Sort the recommendations based on predicted ratings in descending order
recommendations.sort(key=lambda x: x[1], reverse=True)

# Select the top N recommendations
top_recommendations = recommendations[:N]

# Print the top recommendations
print("Top Recommendations:")
for item_id, predicted_rating in top_recommendations:
    movie_title = movie_mappings[movie_mappings.new_id == item_id].index[0]
    print(f"Movie: {movie_title}, Predicted Rating: {predicted_rating}")


Top Recommendations:
Movie: 1377, Predicted Rating: 5.503787040710449
Movie: 1025, Predicted Rating: 5.409177780151367
Movie: 1552, Predicted Rating: 5.379870414733887
Movie: 1222, Predicted Rating: 4.982667446136475
Movie: 780, Predicted Rating: 4.778453826904297


In [ ]:
# Print the top recommendations with movie names
print("Top Recommendations:")
for item_id, predicted_rating in top_recommendations:
    movie_title = movies[movies['movieId'] == item_id]['title'].values[0]
    print(f"Movie: {movie_title}, Predicted Rating: {predicted_rating}")


Top Recommendations:
Movie: Mary Reilly (1996), Predicted Rating: 5.503787040710449
Movie: Mighty Aphrodite (1995), Predicted Rating: 5.409177780151367
Movie: Heidi Fleiss: Hollywood Madam (1995), Predicted Rating: 5.379870414733887
Movie: Crossing Guard, The (1995), Predicted Rating: 4.982667446136475
Movie: Dead Presidents (1995), Predicted Rating: 4.778453826904297


#**Thank You**